# Lab 6.3

Importing libraries

In [1]:
import numpy as np
import pandas as pd
import spotipy
import json
from spotipy.oauth2 import SpotifyClientCredentials
from time import sleep

Getting spotify credentials

In [2]:
%run spotify_client.py

In [9]:
sp = spotipy.Spotify(auth_manager=SpotifyClientCredentials(client_id= client_id,
                                                           client_secret= client_secret))

### search_song

In [4]:
def search_song(title, artist):
    '''function that receives an input of song name and artist and
    searches for results in spotify, gives an output of 5 options to choose
    and returns song_id'''
    
    results = sp.search(q="track:"+title+" artist:"+artist,limit=5)
    
    n = 1
    if results['tracks']['items'] != []:
        for item in results['tracks']['items']:
            print("{}: The name of song is: '{}' and the artist is: {}".format(n, item['name'],item['artists'][0]['name']))
            n += 1
        
        number = int(input('\n Please type the number of your selection:'))
        
        print('\n You selected {} from {}'.format(results['tracks']['items'][(number-1)]['name'], 
                                                  results['tracks']['items'][(number-1)]['artists'][0]['name']))
    
        song_id = results['tracks']['items'][(number-1)]['id']
        
    else: song_id = '', print('Your search didnt retrieve results')
    
    return song_id

In [10]:
test = search_song('creepin', 'metro boomin, the weeknd & 21 savage')

1: The name of song is: 'Creepin' (with The Weeknd & 21 Savage)' and the artist is: Metro Boomin
2: The name of song is: 'Creepin' (with The Weeknd & 21 Savage)' and the artist is: Metro Boomin
3: The name of song is: 'Creepin' (with The Weeknd & 21 Savage)' and the artist is: Metro Boomin
4: The name of song is: 'Creepin' (with The Weeknd & 21 Savage)' and the artist is: Metro Boomin
5: The name of song is: 'Creepin' (with The Weeknd & 21 Savage)' and the artist is: Metro Boomin

 Please type the number of your selection:4

 You selected Creepin' (with The Weeknd & 21 Savage) from Metro Boomin


In [5]:
title = 'killer queen'
artist = 'queen'

In [10]:
results = sp.search(q="track:"+title+" artist:"+artist,limit=1)
results
sp.audio_analysis('1dfeR4HaWDbWqFHLkxsg1d')

HTTP Error for GET to https://api.spotify.com/v1/audio-analysis/1dfeR4HaWDbWqFHLkxsg1d with Params: {} returned 404 due to analysis not found


SpotifyException: http status: 404, code:-1 - https://api.spotify.com/v1/audio-analysis/1dfeR4HaWDbWqFHLkxsg1d:
 analysis not found, reason: None

Reading files

In [11]:
nothot = pd.read_csv('nothot.csv').iloc[:,1:]
hot100 = pd.read_csv('hot100.csv').iloc[:,1:]

In [12]:
nothot.shape

(3950, 3)

### search song, get and add audio features

In [53]:
def search_song_get_add_audio_features(list_of_songs):
    
    # create "chunks" of 50-100 songs
    division = round(len(list_of_songs)/50) #number of chunks
    
    chunks = np.array_split(list_of_songs, division)

    df = pd.DataFrame()

    n=0

    for chunk in chunks:
        print("\n Retrieving id from chunk {} \n".format(n))

        for t,a in zip(chunk['title'], chunk['artist']):
            
            try: 
                results = sp.search(q="track:"+t+" artist:"+a,limit=1)

                my_dict = sp.audio_features(results['tracks']['items'][0]['id'])[0]               

                my_dict_new = { key : [my_dict[key]] for key in list(my_dict.keys()) }

                my_dict_new['title'] = results['tracks']['items'][0]['name'].lower()
                my_dict_new['artist'] = results['tracks']['items'][0]['artists'][0]['name'].lower()

                df = pd.concat([df, pd.DataFrame(my_dict_new)])
                
            except:        
                print('{} from {} was not found'.format(t,a))
            
        sleep(10)
        n += 1
    
    return df

Obtaining audio features for hot_songs dataset.

In [54]:
hot100_audio = search_song_get_add_audio_features(hot100)


 Retrieving id from chunk 0 

i'm good (blue) from david guetta & bebe rexha was not found
rich flex from drake & 21 savage was not found
boy's a liar, pt. 2 from pinkpantheress & ice spice was not found
thank god from kane brown with katelyn brown was not found
escapism from raye featuring 070 shake was not found
calm down from rema & selena gomez was not found
bzrp music sessions, vol. 53 from bizarrap & shakira was not found
wait for u from future featuring drake & tems was not found
i like you (a happier song) from post malone featuring doja cat was not found
bebe dame from fuerza regida x grupo frontera was not found
tomorrow 2 from glorilla & cardi b was not found
wait in the truck from hardy featuring lainey wilson was not found
dawns from zach bryan featuring maggie rogers was not found

 Retrieving id from chunk 1 

que vuelvas from carin leon x grupo frontera was not found
spin bout u from drake & 21 savage was not found
amg from gabito ballesteros, peso pluma & natanael can

In [55]:
pd.set_option('display.max_rows', None)
hot100_audio.reset_index()

danceability  energy  key  loudness  mode  speechiness  acousticness  \
0         0.707   0.681    0    -4.325     1       0.0668       0.06320   
0         0.644   0.728    8    -5.750     1       0.0351       0.05430   
0         0.517   0.675    6    -5.382     1       0.0357       0.45900   
0         0.719   0.454    2    -7.384     1       0.0707       0.01380   
0         0.715   0.620    1    -6.005     0       0.0484       0.41700   
0         0.780   0.689    7    -5.668     1       0.1410       0.03680   
0         0.637   0.643    4    -6.571     1       0.0519       0.13000   
0         0.582   0.525    1    -7.163     0       0.0627       0.11100   
0         0.520   0.731    6    -5.338     0       0.0557       0.34200   
0         0.486   0.545   11    -7.924     1       0.0336       0.06520   
0         0.529   0.695    6    -6.174     1       0.0278       0.48800   
0         0.838   0.525   10    -3.562     1       0.0665       0.34500   
0         0.733   0.690    9    -5.529     0       0.0427       0.06350   
0         0.515   0.593    4    -4.801     1       0.0322       0.65300   
0         0.731   0.850    9    -4.913     1       0.0336       0.25200   
0         0.582   0.568    1    -7.300     1       0.0275       0.57700   
0         0.369   0.192    4   -12.151     0       0.0400       0.55500   
0         0.686   0.507    1    -7.097     1       0.0357       0.62600   
0         0.565   0.560    6    -6.034     1       0.0275       0.53800   
0         0.526   0.606    5    -5.300     0       0.2590       0.15200   
0         0.733   0.436   10   -10.489     1       0.0800       0.25800   
0         0.954   0.516    6    -5.817     1       0.1600       0.03000   
0         0.848   0.512    3    -7.720     0       0.1020       0.22800   
0         0.684   0.607   11    -8.127     0       0.1000       0.02670   
0         0.608   0.745    1    -4.130     1       0.0277       0.02260   
0         0.587   0.632    9    -5.416     1       0.0311       0.14800   
0         0.559   0.551    5    -7.231     1       0.1320       0.14100   
0         0.551   0.550   10    -5.339     1       0.0286       0.77700   
0         0.682   0.805    2    -3.739     1       0.0403       0.08880   
0         0.836   0.743   10    -6.305     0       0.0656       0.09950   
0         0.607   0.912    8    -3.449     1       0.0611       0.12400   
0         0.358   0.284    7    -8.285     1       0.0285       0.80500   
0         0.675   0.726    2    -6.459     1       0.0461       0.10500   
0         0.468   0.779    9    -4.839     1       0.0779       0.11200   
0         0.614   0.913    7    -5.126     1       0.0296       0.00420   
0         0.479   0.768    8    -5.204     1       0.0312       0.00007   
0         0.662   0.398   11    -6.691     0       0.0275       0.71600   
0         0.563   0.851    8    -3.798     1       0.0260       0.00417   
0         0.247   0.299    9    -6.083     1       0.0315       0.89900   
0         0.698   0.546    0    -7.234     0       0.0559       0.42500   
0         0.380   0.488    9    -6.637     1       0.0290       0.12600   
0         0.793   0.780    1    -4.247     0       0.2490       0.34100   
0         0.591   0.637    9    -6.365     0       0.0300       0.01070   
0         0.588   0.931    6    -3.925     1       0.0318       0.00411   
0         0.628   0.632    9    -5.932     1       0.0325       0.25700   
0         0.877   0.517    2    -5.426     0       0.0706       0.21700   
0         0.504   0.736    0    -6.079     1       0.0352       0.00216   
0         0.623   0.466   11    -7.600     1       0.0265       0.04210   
0         0.511   0.600    2    -5.699     1       0.0268       0.16000   
0         0.740   0.697    8    -4.912     1       0.0340       0.02680   
0         0.574   0.469    4    -8.209     1       0.0254       0.53400   
0         0.645   0.534    6   -10.800     0       0.0479       0.15700   
0         0.835   0.679    7

In [61]:
hot100_audio.reset_index(drop=True).to_csv('hot100_audio.csv')

Obtaining audio features for not_hot_songs dataset.

In [57]:
nothot_audio = search_song_get_add_audio_features(nothot)


 Retrieving id from chunk 0 

kebab (feat. fatboy l & asap vergi) from slim mill was not found
debes buscarte un nuevo amor (feat. los mendez) from bryan mevi was not found

 Retrieving id from chunk 1 

nemají mě rádi from s.barracuda was not found
bum bum tam tam from dutty was not found

 Retrieving id from chunk 2 

すみれ september love(2006リマスタリング) from ippu-do was not found
how far i'll go - from "moana" from alessia cara was not found
don't let me down (feat. daya) from the chainsmokers was not found
light it up (feat. nyla & fuse odg) - remix from major lazer was not found
ain't easy - the launch from elijah woods x jamie fine was not found

 Retrieving id from chunk 3 

call on me - ryan riback extended remix from starley was not found
break my heart from dua lipa was not found
i don’t wanna live forever (fifty shades darker) - from "fifty shades darker (original motion picture soundtrack)" from zayn, taylor swift was not found
i'm not the only one from sam smith was not found


HTTP Error for GET to https://api.spotify.com/v1/search with Params: {'q': 'track:love mashup 2019 artist:akhil sachdeva, antara mitra, arijit singh, benny dayal, dhvani bhanushali, karan sehmbi, nikhita gandhi, rahat fateh ali khan, sachet tandon, shreya ghoshal, tulsi kumar, a.r. rahman, amaal mallik, goldboy, mithoon, pritam, rochak kohli, sachet-parampara, sandesh shandilya, sourav roy, tanishk bagchi, dj yogii', 'limit': 1, 'offset': 0, 'type': 'track', 'market': None} returned 400 due to Bad request.


love mashup 2019 from akhil sachdeva, antara mitra, arijit singh, benny dayal, dhvani bhanushali, karan sehmbi, nikhita gandhi, rahat fateh ali khan, sachet tandon, shreya ghoshal, tulsi kumar, a.r. rahman, amaal mallik, goldboy, mithoon, pritam, rochak kohli, sachet-parampara, sandesh shandilya, sourav roy, tanishk bagchi, dj yogii was not found

 Retrieving id from chunk 32 

sigues con el from dímelo flow, arcangel, sech was not found
you're still the one from shania twain was not found

 Retrieving id from chunk 33 

daniel sam from booba was not found

 Retrieving id from chunk 34 

high from madstreet was not found
小幸运 from 陳以桐 was not found
marvin gaye (feat. wale) - remix from charlie puth was not found
run up (feat. partynextdoor & nicki minaj) from major lazer was not found

 Retrieving id from chunk 35 

raabta (title track) [from "raabta"] from pritam, arijit singh, nikhita gandhi was not found
sola (remix) [feat. daddy yankee, wisin, farruko, zion & lennox] from anuel aa w

tattar from shehab, dj totti, dabl de was not found
you are my high from dj snake was not found
stay young from mike perry, tessa odden was not found

 Retrieving id from chunk 66 

hojas de té from pastilla was not found
benz truck - гелик from lil peep was not found
kran turismo (feat. raappana) from jvg was not found
recuerdos from kelmitt, lary over, farruko was not found
i'm bad news from eldar vågan was not found
en mi cuarto from jhay cortez, skrillex was not found

 Retrieving id from chunk 67 

i̇stanbul beyefendisi from yaşlı amca was not found
错位时空 - 治愈版 from 小玄子 was not found
fiel - remix from wisin, jhay cortez, anuel aa, los legendarios, myke towers was not found

 Retrieving id from chunk 68 

don't be shy from tiësto, karol g was not found
can't hold us (feat. ray dalton) from macklemore & ryan lewis, macklemore, ryan lewis was not found
la curiosidad (feat. dj nelson, jhay cortez, lunay & kendo kaponi) - blue grand prix remix from jay wheeler, myke towers, rauw alejand

In [58]:
nothot_audio.reset_index()

danceability  energy  key  loudness  mode  speechiness  acousticness  \
0        0.6710  0.3730    9   -18.064     1       0.0323      0.257000   
0        0.7960  0.8380    8    -5.157     1       0.0574      0.244000   
0        0.7600  0.8380    7    -3.828     0       0.0529      0.547000   
0        0.6930  0.4530    7    -8.262     1       0.0352      0.657000   
0        0.6810  0.3720    5    -8.237     1       0.0432      0.640000   
0        0.5200  0.7610    4    -3.093     1       0.0853      0.256000   
0        0.6940  0.7120    7    -3.923     0       0.0460      0.132000   
0        0.7730  0.7470    5    -4.061     1       0.0885      0.024200   
0        0.5480  0.8470    1    -3.237     1       0.1860      0.062200   
0        0.5320  0.8320   10    -6.047     0       0.0535      0.065200   
0        0.7500  0.5600    8    -8.094     1       0.1050      0.546000   
0        0.8450  0.8680    1    -4.856     1       0.2400      0.275000   
0        0.6830  0.3150    1   -13.394     1       0.0716      0.722000   
0        0.8090  0.6010    5    -5.966     0       0.2710      0.117000   
0        0.7730  0.8200    0    -5.897     0       0.1150      0.394000   
0        0.6660  0.8810    1    -3.137     0       0.1140      0.059700   
0        0.4660  0.9510    5    -3.314     1       0.1250      0.001600   
0        0.7600  0.7730    9    -5.314     1       0.0675      0.176000   
0        0.7640  0.7820   10    -3.925     1       0.1040      0.054400   
0        0.6040  0.7680    7    -6.484     1       0.0308      0.541000   
0        0.7480  0.7880    1    -7.055     1       0.0334      0.059100   
0        0.8070  0.8870    1    -3.892     1       0.2750      0.003810   
0        0.7260  0.4310    8    -8.765     0       0.1350      0.731000   
0        0.6350  0.7130   11    -6.909     1       0.0937      0.228000   
0        0.5420  0.5870    4    -6.145     1       0.0350      0.097700   
0        0.6620  0.5860    0    -8.821     1       0.0307      0.097000   
0        0.6860  0.5420    6    -5.939     0       0.2920      0.346000   
0        0.6530  0.5810    7    -9.164     1       0.0436      0.279000   
0        0.8100  0.4710    9    -7.002     0       0.0470      0.109000   
0        0.8530  0.5600    1    -4.961     1       0.0406      0.013000   
0        0.7650  0.4730   10    -5.829     1       0.0514      0.287000   
0        0.9260  0.7030   11    -6.337     0       0.1030      0.065900   
0        0.7730  0.6540    5    -7.796     0       0.2840      0.530000   
0        0.6490  0.7160    8    -5.371     1       0.0349      0.086300   
0        0.4670  0.9620    2    -2.770     0       0.0356      0.003250   
0        0.7360  0.4490    1   -11.462     0       0.4250      0.330000   
0        0.6420  0.7910    0    -6.073     1       0.1370      0.024200   
0        0.4440  0.8190   10    -4.078     0       0.3410      0.106000   
0        0.6130  0.7640    2    -6.509     1       0.1360      0.052700   
0        0.6700  0.6770    1    -5.554     1       0.0664      0.077100   
0        0.6280  0.6980    6    -5.608     0       0.1050      0.047200   
0        0.5690  0.4910    5    -4.706     1       0.0288      0.434000   
0        0.5050  0.5180    6    -5.622     1       0.0299      0.806000   
0        0.7970  0.5330    0    -9.740     0       0.0412      0.017200   
0        0.5480  0.8860   11    -5.417     0       0.0315      0.000222   
0        0.5830  0.8290    6    -4.715     1       0.1030      0.021800   
0        0.7430  0.7350    8    -5.337     1       0.0382      0.003890   
0        0.5920  0.8990   10    -4.058     0       0.1180      0.034100   
0        0.5730  0.6300    1    -8.389     1       0.1050      0.189000   
0        0.4830  0.7870    8    -5.244     1       0.1020      0.112000   
0        0.2650  0.3120    7   -11.689     1       0.0569      0.243000   
0        0.8140  0.7850   10    -4.566     1       0.0452      0.236000   
0        0.7280  0.5630    1

In [62]:
nothot_audio.reset_index(drop=True).to_csv('nothot_audio.csv')